In [1]:
import polars as pl
import plotly.express as px

# expand polars df output
pl.Config.set_fmt_str_lengths(200)
pl.Config.set_fmt_float("full")

polars.config.Config

In [2]:
cd ../

/home/evan/Documents/preconf_dash


/home/evan/Documents/preconf_dash/.venv/lib/python3.12/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [3]:
def byte_to_string(hex_string):
    if hex_string == "0x":
        return ""
    # Remove the "0x" prefix and decode the hex string
    bytes_object = bytes.fromhex(hex_string[2:])
    try:
        human_readable_string = bytes_object.decode('utf-8')
    except UnicodeDecodeError:
        human_readable_string = bytes_object.decode('latin-1')
    return human_readable_string

In [4]:
# load holesky data
holesky_blocks = pl.scan_parquet(
    'data/blocks.parquet').rename({'number': 'block_number'}).select('block_number', 'timestamp', 'extra_data', 'blob_gas_used', 'excess_blob_gas', 'base_fee_per_gas').with_columns(pl.from_epoch('timestamp'))
holesky_txs = pl.scan_parquet('data/transactions.parquet').select('block_number', 'hash',
                                                                  'to', 'from', 'type', 'gas', 'gas_used', 'gas_price', 'effective_gas_price', 'max_priority_fee_per_gas', 'max_fee_per_gas')

holesky_blocks_txs = (holesky_txs.join(
    holesky_blocks, on='block_number', how='left')
    # .fill_null(strategy="forward")  # forward fill null base fee gas values
    .with_columns(
        (pl.col("base_fee_per_gas") * pl.col("gas_used")).alias("base_tx_fee_eth"),
        (pl.col("effective_gas_price") - pl.col("base_fee_per_gas")).alias(
            "priority_fee_gas"
        )
)
    .with_columns(
        # have to perform priority fee calculation in this column
        (((pl.col("effective_gas_price") - pl.col("base_fee_per_gas"))
          * pl.col("gas_used")) / 10**18).alias("priority_tx_fee_eth"),
        # unit calculations for gwei and eth values
        (pl.col("base_tx_fee_eth") / 10**18).alias("base_tx_fee_eth"),
        (pl.col("priority_fee_gas") / 10**18).alias("priority_fee_gas_eth"),
        (pl.col("base_fee_per_gas") / 10**18).alias("base_fee_per_gas_eth"),
        (pl.col('max_priority_fee_per_gas') / 10 **
         9).alias('max_priority_fee_per_gas_gwei'),
)
    .with_columns(
    pl.col("extra_data").map_elements(byte_to_string,
                                      return_dtype=str).alias("builder_grafiti")
)
    # apply outlier filters
    .filter(pl.col('max_priority_fee_per_gas_gwei') < 200)
    .filter(pl.col('type') == 3)
)

In [5]:
holesky_blobs = holesky_blocks_txs.collect(streaming=True).select(
    'builder_grafiti', 'block_number', 'timestamp', 'type', 'hash', 'from', 'gas_used', 'gas_price', 'effective_gas_price', 'max_priority_fee_per_gas_gwei')

In [27]:
# add sample mempool data in
mempool_df = pl.read_parquet('preconf_blobs/holesky_mempool.parquet').with_columns(pl.col('event_date_time').cast(pl.Datetime("us")))

mempool_blobs = holesky_blobs.join(mempool_df, on='hash', how='inner').with_columns(
    (pl.col('timestamp') - pl.col('event_date_time')).alias('time_in_mempool'),

)

In [29]:
primev_builders = ['preconf.builder', 'preconf.builder2']

The address `0xe51EF1836Dbef052BfFd2eB3Fe1314365d23129d` represents a control group that has a hard time getting blobs included. Parameters are tuned to maximize the amount of time it takes to get included such as having a 6 blob count and very low priority gas fee.

In [31]:
mempool_blobs.filter(pl.col('from') == '0xe51EF1836Dbef052BfFd2eB3Fe1314365d23129d'.lower(
)).shape

(302, 13)

In [37]:
# Filter based on 10 minute inclusion time duration
one_hour_in_microseconds = 1 * 60 * 10 * 1_000_000

In [41]:
# this address is the one using blobs
mempool_blobs.filter(pl.col('from') == '0xe51EF1836Dbef052BfFd2eB3Fe1314365d23129d'.lower(
)).filter(pl.col('time_in_mempool') < one_hour_in_microseconds).sort(by='time_in_mempool', descending=True).head(5)#.filter(pl.col('builder_grafiti').is_in(primev_builders)).group_by('builder_grafiti').agg(pl.len().alias('count'))

shape: (5, 13)
┌────────────┬────────────┬────────────┬──────┬───┬────────────┬───────────┬───────────┬───────────┐
│ builder_gr ┆ block_numb ┆ timestamp  ┆ type ┆ … ┆ max_priori ┆ type_righ ┆ event_dat ┆ time_in_m │
│ afiti      ┆ er         ┆ ---        ┆ ---  ┆   ┆ ty_fee_per ┆ t         ┆ e_time    ┆ empool    │
│ ---        ┆ ---        ┆ datetime[μ ┆ u8   ┆   ┆ _gas_gwei  ┆ ---       ┆ ---       ┆ ---       │
│ str        ┆ u64        ┆ s]         ┆      ┆   ┆ ---        ┆ u8        ┆ datetime[ ┆ duration[ │
│            ┆            ┆            ┆      ┆   ┆ f64        ┆           ┆ μs]       ┆ μs]       │
╞════════════╪════════════╪════════════╪══════╪═══╪════════════╪═══════════╪═══════════╪═══════════╡
│            ┆ 2087071    ┆ 2024-08-07 ┆ 3    ┆ … ┆ 0.1        ┆ 3         ┆ 2024-08-0 ┆ 9m 30s    │
│            ┆            ┆ 17:14:48   ┆      ┆   ┆            ┆           ┆ 7 17:05:1 ┆ 161ms     │
│            ┆            ┆            ┆      ┆   ┆            ┆           ┆ 7.839     ┆           │
│ Øgeth ┆ 2089493    ┆ 2024-08-08 ┆ 3    ┆ … ┆ 0.001      ┆ 3         ┆ 2024-08-0 ┆ 9m 11s    │
│ go1.22.5
 ┆            ┆ 02:05:00   ┆      ┆   ┆            ┆           ┆ 8 01:55:4 ┆ 654ms     │
│ linux      ┆            ┆            ┆      ┆   ┆            ┆           ┆ 8.346     ┆           │
│            ┆ 2087068    ┆ 2024-08-07 ┆ 3    ┆ … ┆ 0.1        ┆ 3         ┆ 2024-08-0 ┆ 9m 11s    │
│            ┆            ┆ 17:14:12   ┆      ┆   ┆            ┆           ┆ 7 17:05:0 ┆ 491ms     │
│            ┆            ┆            ┆      ┆   ┆            ┆           ┆ 0.509     ┆           │
│            ┆ 2087066    ┆ 2024-08-07 ┆ 3    ┆ … ┆ 0.1        ┆ 3         ┆ 2024-08-0 ┆ 9m 2s     │
│            ┆            ┆ 17:13:48   ┆      ┆   ┆            ┆           ┆ 7 17:04:4 ┆ 187ms     │
│            ┆            ┆            ┆      ┆   ┆            ┆           ┆ 5.813     ┆           │
│            ┆ 2087064    ┆ 2024-08-07 ┆ 3    ┆ … ┆ 0.1        ┆ 3         ┆ 2024-08-0 ┆ 8m 52s    │
│            ┆            ┆ 17:13:24   ┆      ┆   ┆            ┆           ┆ 7 17:04:3 ┆ 500ms     │
│            ┆            ┆            ┆      ┆   ┆            ┆           ┆ 1.500     ┆           │
└────────────┴────────────┴────────────┴──────┴───┴────────────┴───────────┴───────────┴───────────┘

In [39]:
mempool_blobs.filter(pl.col('from') == '0xe51EF1836Dbef052BfFd2eB3Fe1314365d23129d'.lower(
)).filter(pl.col('time_in_mempool') < one_hour_in_microseconds).with_columns(
    (pl.col('timestamp') - pl.col('event_date_time')).alias('time_in_mempool'),
).plot.scatter(x='time_in_mempool', y='max_priority_fee_per_gas_gwei')

:Scatter   [time_in_mempool]   (max_priority_fee_per_gas_gwei)

In [42]:
mempool_blobs.filter(pl.col('time_in_mempool') < 12000).plot.scatter(
    x='time_in_mempool', y='max_priority_fee_per_gas_gwei', title='blob time in mempool vs priority fee paid by blobs (gwei, <1 block inclusion)')

:Scatter   [time_in_mempool]   (max_priority_fee_per_gas_gwei)

In [56]:
# How often are blobs submitted per block?
mempool_blobs.group_by('block_number').agg(
    pl.len().alias('blob_per_block_count'),
    pl.col('time_in_mempool').mean().alias('avg_time_in_mempool'),
    pl.col('max_priority_fee_per_gas_gwei').mean().alias(
        'avg_priority_fee_per_gas_gwei'),
).group_by('blob_per_block_count').agg(
    pl.len().alias('count'),
    pl.col('avg_time_in_mempool').mean().alias('avg_time_in_mempool'),
    pl.col('avg_priority_fee_per_gas_gwei').mean().alias(
        'avg_priority_fee_per_gas_gwei'),
).sort(by='blob_per_block_count', descending=True)

shape: (6, 4)
┌──────────────────────┬───────┬─────────────────────┬───────────────────────────────┐
│ blob_per_block_count ┆ count ┆ avg_time_in_mempool ┆ avg_priority_fee_per_gas_gwei │
│ ---                  ┆ ---   ┆ ---                 ┆ ---                           │
│ u32                  ┆ u32   ┆ duration[μs]        ┆ f64                           │
╞══════════════════════╪═══════╪═════════════════════╪═══════════════════════════════╡
│ 6                    ┆ 1237  ┆ 45s 87055µs         ┆ 0.4002763194002969            │
│ 5                    ┆ 894   ┆ 31s 483011µs        ┆ 0.5304573435445181            │
│ 4                    ┆ 2072  ┆ 14s 804199µs        ┆ 0.8243394101352576            │
│ 3                    ┆ 6688  ┆ 11s 558387µs        ┆ 0.9607557560877128            │
│ 2                    ┆ 16339 ┆ 9s 872454µs         ┆ 0.8600686879925897            │
│ 1                    ┆ 23926 ┆ 11s 567307µs        ┆ 0.910735120335535             │
└──────────────────────┴───────┴─────────────────────┴───────────────────────────────┘

In [57]:
mempool_blobs.shape
# only about 10% of blobs take longer than 2 blocks to be included in a block with average fee of 0.58 gwei.

(96848, 13)

In [58]:
# majority of txs make it into holesky before 3 blocks.
print('any time in mempool')
print(mempool_blobs.select('max_priority_fee_per_gas_gwei').mean())

print('time in mempool < 12000')
print(mempool_blobs.filter(pl.col('time_in_mempool') < 12000).select(
    'max_priority_fee_per_gas_gwei').mean())

print('time in mempool > 12000 and < 24000')
print(mempool_blobs.filter(pl.col('time_in_mempool') > 12000).filter(pl.col('time_in_mempool') < 24000).select(
    'max_priority_fee_per_gas_gwei').mean())

print('time in mempool > 24000')
print(mempool_blobs.filter(pl.col('time_in_mempool') > 24000).filter(pl.col('time_in_mempool') < 36000).select(
    'max_priority_fee_per_gas_gwei').mean())

any time in mempool
shape: (1, 1)
┌───────────────────────────────┐
│ max_priority_fee_per_gas_gwei │
│ ---                           │
│ f64                           │
╞═══════════════════════════════╡
│ 0.839937807336734             │
└───────────────────────────────┘
time in mempool < 12000
shape: (1, 1)
┌───────────────────────────────┐
│ max_priority_fee_per_gas_gwei │
│ ---                           │
│ f64                           │
╞═══════════════════════════════╡
│ 1.0319415581776556            │
└───────────────────────────────┘
time in mempool > 12000 and < 24000
shape: (1, 1)
┌───────────────────────────────┐
│ max_priority_fee_per_gas_gwei │
│ ---                           │
│ f64                           │
╞═══════════════════════════════╡
│ 1.03125                       │
└───────────────────────────────┘
time in mempool > 24000
shape: (1, 1)
┌───────────────────────────────┐
│ max_priority_fee_per_gas_gwei │
│ ---                           │
│ f64                   

In [59]:
import holoviews as hv

mempool_time_plot = mempool_blobs.plot.scatter(
    x='time_in_mempool', y='max_priority_fee_per_gas_gwei', title='blob time in mempool vs priority fee paid by blobs (gwei)')

# Define the horizontal line
hline = hv.VLine(12000).opts(color='red', line_width=2, line_dash='dashed')

# Overlay the horizontal line on the plot
final_plot = mempool_time_plot * hline

In [60]:
final_plot

:Overlay
   .Scatter.I :Scatter   [time_in_mempool]   (max_priority_fee_per_gas_gwei)
   .VLine.I   :VLine   [x,y]

In [61]:
mempool_blobs.with_columns(
    (pl.col('timestamp') - pl.col('event_date_time')).alias('time_in_mempool'),
)

shape: (96_848, 13)
┌────────────┬────────────┬────────────┬──────┬───┬────────────┬───────────┬───────────┬───────────┐
│ builder_gr ┆ block_numb ┆ timestamp  ┆ type ┆ … ┆ max_priori ┆ type_righ ┆ event_dat ┆ time_in_m │
│ afiti      ┆ er         ┆ ---        ┆ ---  ┆   ┆ ty_fee_per ┆ t         ┆ e_time    ┆ empool    │
│ ---        ┆ ---        ┆ datetime[μ ┆ u8   ┆   ┆ _gas_gwei  ┆ ---       ┆ ---       ┆ ---       │
│ str        ┆ u64        ┆ s]         ┆      ┆   ┆ ---        ┆ u8        ┆ datetime[ ┆ duration[ │
│            ┆            ┆            ┆      ┆   ┆ f64        ┆           ┆ μs]       ┆ μs]       │
╞════════════╪════════════╪════════════╪══════╪═══╪════════════╪═══════════╪═══════════╪═══════════╡
│ Titan (tit ┆ 2052952    ┆ 2024-08-02 ┆ 3    ┆ … ┆ 1          ┆ 3         ┆ 2024-08-0 ┆ 8s 678ms  │
│ anbuilder. ┆            ┆ 14:30:12   ┆      ┆   ┆            ┆           ┆ 2 14:30:0 ┆           │
│ xyz)       ┆            ┆            ┆      ┆   ┆            ┆           ┆ 3.322     ┆           │
│ Titan (tit ┆ 2052952    ┆ 2024-08-02 ┆ 3    ┆ … ┆ 1          ┆ 3         ┆ 2024-08-0 ┆ 6s 666ms  │
│ anbuilder. ┆            ┆ 14:30:12   ┆      ┆   ┆            ┆           ┆ 2 14:30:0 ┆           │
│ xyz)       ┆            ┆            ┆      ┆   ┆            ┆           ┆ 5.334     ┆           │
│            ┆ 2052953    ┆ 2024-08-02 ┆ 3    ┆ … ┆ 1          ┆ 3         ┆ 2024-08-0 ┆ 8s 786ms  │
│            ┆            ┆ 14:30:24   ┆      ┆   ┆            ┆           ┆ 2 14:30:1 ┆           │
│            ┆            ┆            ┆      ┆   ┆            ┆           ┆ 5.214     ┆           │
│            ┆ 2052955    ┆ 2024-08-02 ┆ 3    ┆ … ┆ 1          ┆ 3         ┆ 2024-08-0 ┆ 20s 593ms │
│            ┆            ┆ 14:31:00   ┆      ┆   ┆            ┆           ┆ 2 14:30:3 ┆           │
│            ┆            ┆            ┆      ┆   ┆            ┆           ┆ 9.407     ┆           │
│            ┆ 2052955    ┆ 2024-08-02 ┆ 3    ┆ … ┆ 1          ┆ 3         ┆ 2024-08-0 ┆ 3s 761ms  │
│            ┆            ┆ 14:31:00   ┆      ┆   ┆            ┆           ┆ 2 14:30:5 ┆           │
│            ┆            ┆            ┆      ┆   ┆            ┆           ┆ 6.239     ┆           │
│ …          ┆ …          ┆ …          ┆ …    ┆ … ┆ …          ┆ …         ┆ …         ┆ …         │
│ Titan (tit ┆ 2118511    ┆ 2024-08-12 ┆ 3    ┆ … ┆ 1          ┆ 3         ┆ 2024-08-1 ┆ 10s 121ms │
│ anbuilder. ┆            ┆ 14:19:00   ┆      ┆   ┆            ┆           ┆ 2 14:18:4 ┆           │
│ xyz)       ┆            ┆            ┆      ┆   ┆            ┆           ┆ 9.879     ┆           │
│ Nethermind ┆ 2118512    ┆ 2024-08-12 ┆ 3    ┆ … ┆ 1          ┆ 3         ┆ 2024-08-1 ┆ 1s 743ms  │
│            ┆            ┆ 14:19:12   ┆      ┆   ┆            ┆           ┆ 2 14:19:1 ┆           │
│            ┆            ┆            ┆      ┆   ┆            ┆           ┆ 0.257     ┆           │
│ reth/v1.0. ┆ 2118513    ┆ 2024-08-12 ┆ 3    ┆ … ┆ 1          ┆ 3         ┆ 2024-08-1 ┆ 8s 754ms  │
│ 3/linux    ┆            ┆ 14:19:24   ┆      ┆   ┆            ┆           ┆ 2 14:19:1 ┆           │
│            ┆            ┆            ┆      ┆   ┆            ┆           ┆ 5.246     ┆           │
│ reth/v1.0. ┆ 2118513    ┆ 2024-08-12 ┆ 3    ┆ … ┆ 1          ┆ 3         ┆ 2024-08-1 ┆ -342ms    │
│ 3/linux    ┆            ┆ 14:19:24   ┆      ┆   ┆            ┆           ┆ 2 14:19:2 ┆           │
│            ┆            ┆            ┆      ┆   ┆            ┆           ┆ 4.342     ┆           │
│ Nethermind ┆ 2118514    ┆ 2024-08-12 ┆ 3    ┆ … ┆ 1          ┆ 3         ┆ 2024-08-1 ┆ 23s 22ms  │
│            ┆            ┆ 14:19:48   ┆      ┆   ┆            ┆           ┆ 2 14:19:2 ┆           │
│            ┆            ┆            ┆      ┆   ┆            ┆           ┆ 4.978     ┆           │
└────────────┴────────────┴────────────┴──────┴───┴────────────┴───────────┴───────────┴───────────┘

In [62]:
final_plot

:Overlay
   .Scatter.I :Scatter   [time_in_mempool]   (max_priority_fee_per_gas_gwei)
   .VLine.I   :VLine   [x,y]

### mev-commit 0.4.3 preconf data

In [64]:
preconf_df = pl.read_parquet('preconf_blobs/preconfs_0.4.3.parquet')

In [67]:
preconf_decay_df =(
    preconf_df
    # calculate bid latency
    .with_columns(
        (pl.from_epoch('dispatchTimestamp',
                       time_unit='ms')).dt.round('1s').alias('datetime'),
        (pl.col('dispatchTimestamp') - \
         pl.col('decayStartTimeStamp')).alias('bid_latency'),
        (pl.col('bid')/10**18).alias('bid_eth'),
        (pl.col('decayEndTimeStamp') -
         pl.col('decayStartTimeStamp')).alias('total_decay_range'),
        # if decay_time_past is negative, it means that the provider commited outside of the decay range so the bid would have fully decayed to 0.
        (pl.col('decayEndTimeStamp') -
         pl.col('dispatchTimestamp')).alias('decay_time_past'),
    )
    .with_columns(
        # total decay time is the range [beginDecayTimestamp, endDecayTimestamp] and `decay_time_past` is the time the provider commited to the transaction.
        (1 - (pl.col('decay_time_past') / pl.col('total_decay_range'))
         ).alias('decay_percent')
    )
    .with_columns(
        (pl.col('bid') * pl.col('decay_percent') / 10**18).alias('decayed_bid_eth'),
    )
)

In [89]:
# checking my bidder stats
preconf_decay_df.filter(pl.col('bidder') == '0xe51ef1836dbef052bffd2eb3fe1314365d23129d').select('bid_latency').mean()

shape: (1, 1)
┌───────────────────┐
│ bid_latency       │
│ ---               │
│ f64               │
╞═══════════════════╡
│ 288.3826754385965 │
└───────────────────┘

In [95]:
preconf_decay_df.filter(pl.col('bidder') == '0xe51ef1836dbef052bffd2eb3fe1314365d23129d').filter(pl.col('blockNumber') > 2046515)

shape: (832, 25)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ block_num ┆ blockNumb ┆ txnHash   ┆ bid       ┆ … ┆ total_dec ┆ decay_tim ┆ decay_per ┆ decayed_ │
│ ber       ┆ er        ┆ ---       ┆ ---       ┆   ┆ ay_range  ┆ e_past    ┆ cent      ┆ bid_eth  │
│ ---       ┆ ---       ┆ str       ┆ u64       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---      │
│ u64       ┆ u64       ┆           ┆           ┆   ┆ u64       ┆ u64       ┆ f64       ┆ f64      │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 11581145  ┆ 2079527   ┆ 0x458883f ┆ 250000000 ┆ … ┆ 8000      ┆ 7577      ┆ 0.0528750 ┆ 0.001321 │
│           ┆           ┆ d36170617 ┆ 00000000  ┆   ┆           ┆           ┆ 000000000 ┆ 87500000 │
│           ┆           ┆ 05dad6133 ┆           ┆   ┆           ┆           ┆ 05        ┆ 00004    │
│           ┆           ┆ 9c029294e ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ 143005770 ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ 81f3cbd85 ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ 593a96b8e ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ a61       ┆           ┆   ┆           ┆           ┆           ┆          │
│ 11636632  ┆ 2080406   ┆ 0xf182bb5 ┆ 250000000 ┆ … ┆ 8000      ┆ 7763      ┆ 0.0296250 ┆ 0.000740 │
│           ┆           ┆ b788ebd3e ┆ 00000000  ┆   ┆           ┆           ┆ 000000000 ┆ 62500000 │
│           ┆           ┆ f9e838132 ┆           ┆   ┆           ┆           ┆ 12        ┆ 00003    │
│           ┆           ┆ 03d29cbd5 ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ 1023fe3bd ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ 073ec767b ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ ad464590d ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ 298       ┆           ┆   ┆           ┆           ┆           ┆          │
│ 11637106  ┆ 2080414   ┆ 0x1892705 ┆ 250000000 ┆ … ┆ 8000      ┆ 7759      ┆ 0.0301249 ┆ 0.000753 │
│           ┆           ┆ acd86c44f ┆ 00000000  ┆   ┆           ┆           ┆ 999999999 ┆ 12499999 │
│           ┆           ┆ defc03cc3 ┆           ┆   ┆           ┆           ┆ 57        ┆ 99989    │
│           ┆           ┆ b389ba596 ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ 0a7f7eb78 ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ 89887b485 ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ b3e1319f0 ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ f1f       ┆           ┆   ┆           ┆           ┆           ┆          │
│ 11638056  ┆ 2080429   ┆ 0xf064e58 ┆ 250000000 ┆ … ┆ 8000      ┆ 7764      ┆ 0.0294999 ┆ 0.000737 │
│           ┆           ┆ 463b41e37 ┆ 00000000  ┆   ┆           ┆           ┆ 999999999 ┆ 49999999 │
│           ┆           ┆ adbc1da96 ┆           ┆   ┆           ┆           ┆ 7         ┆ 99993    │
│           ┆           ┆ 5fb1ff696 ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ df0b0dd98 ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ 5a3a5d615 ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ 8d1a8b0e6 ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ ab2       ┆           ┆   ┆           ┆           ┆           ┆          │
│ 11638551  ┆ 2080436   ┆ 0xb43a9a2 ┆ 250000000 ┆ … ┆ 8000      ┆ 7620      ┆ 0.0474999 ┆ 0.001187 │
│           ┆           ┆ bc6cdc34e ┆ 000000

In [96]:
preconf_decay_df.filter(pl.col('bidder') == '0xe51ef1836dbef052bffd2eb3fe1314365d23129d').filter(pl.col('blockNumber') > 2046515).group_by('commiter', 'isSlash').agg(pl.len().alias('count'))

shape: (3, 3)
┌────────────────────────────────────────────┬─────────┬───────┐
│ commiter                                   ┆ isSlash ┆ count │
│ ---                                        ┆ ---     ┆ ---   │
│ str                                        ┆ bool    ┆ u32   │
╞════════════════════════════════════════════╪═════════╪═══════╡
│ 0x8280f34750068c67acf5366a5c7caea554c36fb5 ┆ true    ┆ 405   │
│ 0x8280f34750068c67acf5366a5c7caea554c36fb5 ┆ false   ┆ 1     │
│ 0x2445e5e28890de3e93f39fca817639c470f4d3b9 ┆ true    ┆ 426   │
└────────────────────────────────────────────┴─────────┴───────┘

In [106]:
preconf_decay_df.filter(pl.col('bidder') == '0xe51ef1836dbef052bffd2eb3fe1314365d23129d').filter(pl.col('blockNumber') > 2046515).filter(pl.col('isSlash') == True).group_by('txnHash', 'commiter').agg(pl.len().alias('count')).sort(by='count', descending=True)

shape: (84, 3)
┌─────────────────────────────────────────────┬────────────────────────────────────────────┬───────┐
│ txnHash                                     ┆ commiter                                   ┆ count │
│ ---                                         ┆ ---                                        ┆ ---   │
│ str                                         ┆ str                                        ┆ u32   │
╞═════════════════════════════════════════════╪════════════════════════════════════════════╪═══════╡
│ 0x8a2713a8b9ee1537dd5867e8ecc36297b1f3292fa ┆ 0x2445e5e28890de3e93f39fca817639c470f4d3b9 ┆ 189   │
│ d582e72fc4f3a8197a2ac76                     ┆                                            ┆       │
│ 0x8a2713a8b9ee1537dd5867e8ecc36297b1f3292fa ┆ 0x8280f34750068c67acf5366a5c7caea554c36fb5 ┆ 138   │
│ d582e72fc4f3a8197a2ac76                     ┆                                            ┆       │
│ 0xbbf76bfc89334ef1132cec3e76f541a4f468baff0 ┆ 0x8280f34750068c67acf5366a5c7caea554c36fb5 ┆ 72    │
│ 293ce6eeeab7014e41ae636                     ┆                                            ┆       │
│ 0xbbf76bfc89334ef1132cec3e76f541a4f468baff0 ┆ 0x2445e5e28890de3e93f39fca817639c470f4d3b9 ┆ 41    │
│ 293ce6eeeab7014e41ae636                     ┆                                            ┆       │
│ 0xab3f3379b6f19ed6ddeddc76439d42dd82bff4641 ┆ 0x8280f34750068c67acf5366a5c7caea554c36fb5 ┆ 27    │
│ 8cd0182c9c21e1042fb7da8                     ┆                                            ┆       │
│ …                                           ┆ …                                          ┆ …     │
│ 0x1ce4f0d9c7c2bf542c7a601e8ebd6103b1bafe5d2 ┆ 0x8280f34750068c67acf5366a5c7caea554c36fb5 ┆ 1     │
│ 31b0a9e17a91df62ccfd6b4                     ┆                                            ┆       │
│ 0x767827063b058ee4bea36526dbd8d55fa54c01db1 ┆ 0x8280f34750068c67acf5366a5c7caea554c36fb5 ┆ 1     │
│ 5cd7591b2c1bbbde041779a                     ┆                                            ┆       │
│ 0xd77c1aeca156274535a57d247093d2ddec8033a1e ┆ 0x8280f34750068c67acf5366a5c7caea554c36fb5 ┆ 1     │
│ eb84df2672a652138b69c51                     ┆                                            ┆       │
│ 0x142e4a1341787ea99e6cec22d27f60fab3d5ec1c7 ┆ 0x8280f34750068c67acf5366a5c7caea554c36fb5 ┆ 1     │
│ 00a7ff99d3ad4449faca3a9                     ┆                                            ┆       │
│ 0xe1867bc9c7fe658228560e887e08cfdfc765a6a4d ┆ 0x8280f34750068c67acf5366a5c7caea554c36fb5 ┆ 1     │
│ 108074a30f7e4f47e676f61                     ┆                                            ┆       │
└─────────────────────────────────────────────┴────────────────────────────────────────────┴───────┘

In [100]:
mempool_blobs.filter(pl.col('hash') == '0x458883fd3617061705dad61339c029294e14300577081f3cbd85593a96b8ea61')

shape: (1, 13)
┌────────────┬────────────┬────────────┬──────┬───┬────────────┬───────────┬───────────┬───────────┐
│ builder_gr ┆ block_numb ┆ timestamp  ┆ type ┆ … ┆ max_priori ┆ type_righ ┆ event_dat ┆ time_in_m │
│ afiti      ┆ er         ┆ ---        ┆ ---  ┆   ┆ ty_fee_per ┆ t         ┆ e_time    ┆ empool    │
│ ---        ┆ ---        ┆ datetime[μ ┆ u8   ┆   ┆ _gas_gwei  ┆ ---       ┆ ---       ┆ ---       │
│ str        ┆ u64        ┆ s]         ┆      ┆   ┆ ---        ┆ u8        ┆ datetime[ ┆ duration[ │
│            ┆            ┆            ┆      ┆   ┆ f64        ┆           ┆ μs]       ┆ μs]       │
╞════════════╪════════════╪════════════╪══════╪═══╪════════════╪═══════════╪═══════════╪═══════════╡
│ preconf.bu ┆ 2079527    ┆ 2024-08-06 ┆ 3    ┆ … ┆ 1          ┆ 3         ┆ 2024-08-0 ┆ 1s 204ms  │
│ ilder2     ┆            ┆ 14:14:00   ┆      ┆   ┆            ┆           ┆ 6 14:13:5 ┆           │
│            ┆            ┆            ┆      ┆   ┆            ┆           ┆ 8.796     ┆           │
└────────────┴────────────┴────────────┴──────┴───┴────────────┴───────────┴───────────┴───────────┘